## Finding grammatical role of sentences

In [1]:
# Import dependencies
import requests
import json
import os
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import pandas as pd
import contractions
from tqdm import tqdm
import string
import collections
import numpy as np
from keras import backend as K
from keras.models import Sequential, Model
from keras.layers.wrappers import TimeDistributed, Bidirectional, Layer
from keras.layers import Dense, Dropout, Embedding, Input
from keras.layers.core import Activation, RepeatVector, Permute, Reshape
from keras.layers.recurrent import LSTM
from keras.optimizers import RMSprop
import argparse
import numpy.random as randm
from keras.utils import np_utils

Using TensorFlow backend.
/home/dheeraj/.local/lib/python3.5/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/dheeraj/.local/lib/python3.5/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/dheeraj/.local/lib/python3.5/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/dheeraj/.local/lib/python3.5/site-packages/tensorflow/py

In [2]:

def get_sentences(text):
    annotators = 'pos,parse,ssplit'
    properties = {'annotators': annotators, 'outputFormat': 'json'}
    params = {'properties': str(properties), 'pipelineLanguage': 'en'}
    text = text.encode('utf-8')
    r = requests.post("http://localhost:9000", params=params, data=text, headers={'Connection': 'close'})
    r_dict = json.loads(r.text)
    sentences  = []
    gr = []
    for sent in r_dict['sentences']:
        start_offset = sent['tokens'][0]['characterOffsetBegin'] # Begin offset of first token.
        end_offset = sent['tokens'][-1]['characterOffsetEnd'] # End offset of last token.
        sent_str = text[start_offset:end_offset]
        
        # Preprocessing sentence 
        # 1. remove '/n'
        # 2. lowercase
        # 3. contraction expansion
        sent_str = contractions.fix(sent_str.decode("utf-8")).replace("\n"," ").lower().strip()
        gr_request = requests.post("http://localhost:9000", params=params, data=sent_str.encode("utf-8"), headers={'Connection': 'close'})
        gr_dict = json.loads(gr_request.text)
        if sent_str:
            relations = gr_dict['sentences'][0]['basicDependencies']
            new_words = [0] * len(relations)
            word_gr = [0] * len(relations)
            for relation in relations:
                clas = relation['dep']
                index = int(relation['dependent'])
                new_words[index-1] = relation['dependentGloss']
                word_gr[index-1] = clas
            sentences.append(' '.join(new_words))
            gr.append(word_gr)
        
    return sentences, gr

## Preparing Data GCDC

In [3]:
# Get clinton data

df_clinton = pd.read_csv("Data/Clinton_train.csv")
df_enron = pd.read_csv("Data/Enron_train.csv")
df_train = df_clinton.append(df_enron)
df_test_clinton = pd.read_csv("Data/Enron_test.csv")
df_test_enron = pd.read_csv("Data/Clinton_test.csv")


In [18]:
documents = list(df_train['text'])
label = list(map(int, df_train['labelA']))


In [175]:
# Preprocessing data
# Convert documents to sentences
# Get G.R of each sentences

new_documents = []

for i in tqdm(documents):
    new_documents.append(get_sentences(i))
    











  0%|          | 0/2000 [00:00<?, ?it/s]









  0%|          | 1/2000 [00:08<4:52:06,  8.77s/it]









  0%|          | 2/2000 [00:28<6:46:02, 12.19s/it]









  0%|          | 3/2000 [00:31<5:13:15,  9.41s/it]









  0%|          | 4/2000 [00:33<3:52:32,  6.99s/it]









  0%|          | 5/2000 [00:33<2:50:01,  5.11s/it]









  0%|          | 6/2000 [00:36<2:22:28,  4.29s/it]









  0%|          | 7/2000 [00:56<5:02:02,  9.09s/it]









  0%|          | 8/2000 [00:59<3:55:31,  7.09s/it]









  0%|          | 9/2000 [01:01<3:08:00,  5.67s/it]









  0%|          | 10/2000 [01:03<2:29:02,  4.49s/it]









  1%|          | 11/2000 [01:04<1:54:40,  3.46s/it]









  1%|          | 12/2000 [01:05<1:37:47,  2.95s/it]









  1%|          | 13/2000 [01:07<1:22:07,  2.48s/it]









  1%|          | 14/2000 [01:09<1:15:50,  2.29s/it]









  1%|          | 15/2000 [01:12<1:25:12,  2.58s/it]









  1%|          | 16/2000 [01:13<1:

  9%|▉         | 179/2000 [09:29<1:45:04,  3.46s/it]









  9%|▉         | 180/2000 [09:29<1:21:33,  2.69s/it]









  9%|▉         | 181/2000 [09:31<1:12:40,  2.40s/it]









  9%|▉         | 182/2000 [09:33<1:07:53,  2.24s/it]









  9%|▉         | 183/2000 [09:35<1:06:59,  2.21s/it]









  9%|▉         | 184/2000 [09:38<1:09:14,  2.29s/it]









  9%|▉         | 185/2000 [09:45<1:58:52,  3.93s/it]









  9%|▉         | 186/2000 [09:48<1:43:51,  3.44s/it]









  9%|▉         | 187/2000 [09:49<1:24:20,  2.79s/it]









  9%|▉         | 188/2000 [09:51<1:19:12,  2.62s/it]









  9%|▉         | 189/2000 [09:55<1:33:07,  3.09s/it]









 10%|▉         | 190/2000 [09:57<1:18:41,  2.61s/it]









 10%|▉         | 191/2000 [09:59<1:14:12,  2.46s/it]









 10%|▉         | 192/2000 [10:01<1:13:05,  2.43s/it]









 10%|▉         | 193/2000 [10:02<56:44,  1.88s/it]  









 10%|▉         | 194/2000 [10:04<1:01:33,  2.05s/it]









 10%|▉  

 18%|█▊        | 357/2000 [17:39<36:38,  1.34s/it]









 18%|█▊        | 358/2000 [17:53<2:18:40,  5.07s/it]









 18%|█▊        | 359/2000 [17:56<2:04:07,  4.54s/it]









 18%|█▊        | 360/2000 [17:59<1:45:30,  3.86s/it]









 18%|█▊        | 361/2000 [18:08<2:31:42,  5.55s/it]









 18%|█▊        | 362/2000 [18:10<2:01:47,  4.46s/it]









 18%|█▊        | 363/2000 [18:11<1:35:43,  3.51s/it]









 18%|█▊        | 364/2000 [18:13<1:20:02,  2.94s/it]









 18%|█▊        | 365/2000 [18:19<1:49:31,  4.02s/it]









 18%|█▊        | 366/2000 [18:22<1:36:10,  3.53s/it]









 18%|█▊        | 367/2000 [18:40<3:36:43,  7.96s/it]









 18%|█▊        | 368/2000 [18:41<2:42:41,  5.98s/it]









 18%|█▊        | 369/2000 [18:44<2:13:01,  4.89s/it]









 18%|█▊        | 370/2000 [18:46<1:50:20,  4.06s/it]









 19%|█▊        | 371/2000 [18:55<2:34:09,  5.68s/it]









 19%|█▊        | 372/2000 [18:56<1:56:34,  4.30s/it]









 19%|█▊   

 27%|██▋       | 535/2000 [27:21<1:31:34,  3.75s/it]









 27%|██▋       | 536/2000 [27:23<1:19:57,  3.28s/it]









 27%|██▋       | 537/2000 [27:33<2:04:03,  5.09s/it]









 27%|██▋       | 538/2000 [27:34<1:37:33,  4.00s/it]









 27%|██▋       | 539/2000 [27:37<1:27:16,  3.58s/it]









 27%|██▋       | 540/2000 [27:41<1:29:49,  3.69s/it]









 27%|██▋       | 541/2000 [27:48<1:56:55,  4.81s/it]









 27%|██▋       | 542/2000 [27:50<1:38:07,  4.04s/it]









 27%|██▋       | 543/2000 [27:52<1:20:59,  3.34s/it]









 27%|██▋       | 544/2000 [27:53<1:04:40,  2.66s/it]









 27%|██▋       | 545/2000 [27:56<1:09:40,  2.87s/it]









 27%|██▋       | 546/2000 [27:59<1:05:15,  2.69s/it]









 27%|██▋       | 547/2000 [28:00<52:06,  2.15s/it]  









 27%|██▋       | 548/2000 [28:00<41:41,  1.72s/it]









 27%|██▋       | 549/2000 [28:04<54:53,  2.27s/it]









 28%|██▊       | 550/2000 [28:07<59:53,  2.48s/it]









 28%|██▊      

 31%|███▏      | 625/2000 [31:37<1:21:07,  3.54s/it]









 31%|███▏      | 626/2000 [31:42<1:32:55,  4.06s/it]









 31%|███▏      | 627/2000 [31:45<1:23:48,  3.66s/it]









 31%|███▏      | 628/2000 [31:46<1:04:53,  2.84s/it]









 31%|███▏      | 629/2000 [31:48<56:56,  2.49s/it]  









 32%|███▏      | 630/2000 [31:49<51:19,  2.25s/it]









 32%|███▏      | 631/2000 [31:50<42:24,  1.86s/it]









 32%|███▏      | 632/2000 [31:51<35:50,  1.57s/it]









 32%|███▏      | 633/2000 [31:52<32:50,  1.44s/it]









 32%|███▏      | 634/2000 [31:54<38:14,  1.68s/it]









 32%|███▏      | 635/2000 [31:56<39:08,  1.72s/it]









 32%|███▏      | 636/2000 [31:59<43:03,  1.89s/it]









 32%|███▏      | 637/2000 [32:04<1:07:05,  2.95s/it]









 32%|███▏      | 638/2000 [32:12<1:41:17,  4.46s/it]









 32%|███▏      | 639/2000 [32:16<1:37:24,  4.29s/it]









 32%|███▏      | 640/2000 [32:21<1:42:22,  4.52s/it]









 32%|███▏      | 641/2

...

 67%|██████▋   | 1335/2000 [1:13:05<28:43,  2.59s/it]









 67%|██████▋   | 1336/2000 [1:13:08<28:50,  2.61s/it]









 67%|██████▋   | 1337/2000 [1:13:11<30:29,  2.76s/it]









 67%|██████▋   | 1338/2000 [1:13:13<25:45,  2.33s/it]









 67%|██████▋   | 1339/2000 [1:13:13<20:16,  1.84s/it]









 67%|██████▋   | 1340/2000 [1:13:15<20:02,  1.82s/it]









 67%|██████▋   | 1341/2000 [1:13:17<22:00,  2.00s/it]









 67%|██████▋   | 1342/2000 [1:13:18<18:48,  1.72s/it]









 67%|██████▋   | 1343/2000 [1:13:25<35:21,  3.23s/it]









 67%|██████▋   | 1344/2000 [1:13:28<32:59,  3.02s/it]









 67%|██████▋   | 1345/2000 [1:13:31<34:33,  3.17s/it]









 67%|██████▋   | 1346/2000 [1:13:34<33:22,  3.06s/it]









 67%|██████▋   | 1347/2000 [1:13:36<29:39,  2.73s/it]









 67%|██████▋   | 1348/2000 [1:13:49<1:01:35,  5.67s/it]









 67%|██████▋   | 1349/2000 [1:13:50<48:42,  4.49s/it]  









 68%|██████▊   | 1350/2000 [1:13:52<38:49,  3.58s/i

 76%|███████▌  | 1510/2000 [1:24:16<16:46,  2.05s/it]









 76%|███████▌  | 1511/2000 [1:24:18<15:24,  1.89s/it]









 76%|███████▌  | 1512/2000 [1:24:20<15:09,  1.86s/it]









 76%|███████▌  | 1513/2000 [1:24:21<13:42,  1.69s/it]









 76%|███████▌  | 1514/2000 [1:24:53<1:26:23, 10.67s/it]









 76%|███████▌  | 1515/2000 [1:24:57<1:12:20,  8.95s/it]









 76%|███████▌  | 1516/2000 [1:24:59<53:45,  6.66s/it]  









 76%|███████▌  | 1517/2000 [1:25:01<42:46,  5.31s/it]









 76%|███████▌  | 1518/2000 [1:25:06<40:51,  5.09s/it]









 76%|███████▌  | 1519/2000 [1:25:08<33:43,  4.21s/it]









 76%|███████▌  | 1520/2000 [1:25:13<36:21,  4.54s/it]









 76%|███████▌  | 1521/2000 [1:25:15<31:13,  3.91s/it]









 76%|███████▌  | 1522/2000 [1:25:19<31:24,  3.94s/it]









 76%|███████▌  | 1523/2000 [1:25:21<26:30,  3.33s/it]









 76%|███████▌  | 1524/2000 [1:25:22<20:42,  2.61s/it]









 76%|███████▋  | 1525/2000 [1:25:24<18:58,  2.40s

 80%|███████▉  | 1598/2000 [1:29:15<21:42,  3.24s/it]









 80%|███████▉  | 1599/2000 [1:29:17<18:30,  2.77s/it]









 80%|████████  | 1600/2000 [1:29:19<16:05,  2.41s/it]









 80%|████████  | 1601/2000 [1:29:20<14:06,  2.12s/it]









 80%|████████  | 1602/2000 [1:29:21<12:23,  1.87s/it]









 80%|████████  | 1603/2000 [1:29:29<23:27,  3.55s/it]









 80%|████████  | 1604/2000 [1:29:35<27:49,  4.22s/it]









 80%|████████  | 1605/2000 [1:29:36<22:04,  3.35s/it]









 80%|████████  | 1606/2000 [1:29:44<31:29,  4.79s/it]









 80%|████████  | 1607/2000 [1:29:48<30:32,  4.66s/it]









 80%|████████  | 1608/2000 [1:29:49<23:11,  3.55s/it]









 80%|████████  | 1609/2000 [1:30:50<2:14:37, 20.66s/it]









 80%|████████  | 1610/2000 [1:30:51<1:36:38, 14.87s/it]









 81%|████████  | 1611/2000 [1:30:53<1:10:49, 10.93s/it]









 81%|████████  | 1612/2000 [1:30:54<52:08,  8.06s/it]  









 81%|████████  | 1613/2000 [1:30:57<40:41,  6.3

 89%|████████▊ | 1774/2000 [1:38:34<10:44,  2.85s/it]









 89%|████████▉ | 1775/2000 [1:38:36<09:15,  2.47s/it]









 89%|████████▉ | 1776/2000 [1:38:39<09:15,  2.48s/it]









 89%|████████▉ | 1777/2000 [1:38:41<08:52,  2.39s/it]









 89%|████████▉ | 1778/2000 [1:38:43<08:53,  2.41s/it]









 89%|████████▉ | 1779/2000 [1:38:44<07:33,  2.05s/it]









 89%|████████▉ | 1780/2000 [1:38:45<06:18,  1.72s/it]









 89%|████████▉ | 1781/2000 [1:38:48<07:13,  1.98s/it]









 89%|████████▉ | 1782/2000 [1:38:49<06:15,  1.72s/it]









 89%|████████▉ | 1783/2000 [1:38:53<08:40,  2.40s/it]









 89%|████████▉ | 1784/2000 [1:38:54<07:03,  1.96s/it]









 89%|████████▉ | 1785/2000 [1:38:58<08:45,  2.44s/it]









 89%|████████▉ | 1786/2000 [1:39:06<14:55,  4.19s/it]









 89%|████████▉ | 1787/2000 [1:39:08<12:18,  3.47s/it]









 89%|████████▉ | 1788/2000 [1:39:15<15:56,  4.51s/it]









 89%|████████▉ | 1789/2000 [1:39:17<13:22,  3.80s/it]



 98%|█████████▊| 1950/2000 [1:52:45<05:34,  6.69s/it]









 98%|█████████▊| 1951/2000 [1:52:46<04:04,  5.00s/it]









 98%|█████████▊| 1952/2000 [1:52:48<03:12,  4.02s/it]









 98%|█████████▊| 1953/2000 [1:52:52<03:06,  3.97s/it]









 98%|█████████▊| 1954/2000 [1:52:54<02:32,  3.31s/it]









 98%|█████████▊| 1955/2000 [1:52:56<02:13,  2.96s/it]









 98%|█████████▊| 1956/2000 [1:53:29<08:47, 11.98s/it]









 98%|█████████▊| 1957/2000 [1:53:32<06:47,  9.47s/it]









 98%|█████████▊| 1958/2000 [1:53:41<06:31,  9.33s/it]









 98%|█████████▊| 1959/2000 [1:53:43<04:52,  7.13s/it]









 98%|█████████▊| 1960/2000 [1:53:48<04:12,  6.30s/it]









 98%|█████████▊| 1961/2000 [1:53:49<03:09,  4.87s/it]









 98%|█████████▊| 1962/2000 [1:53:52<02:36,  4.11s/it]









 98%|█████████▊| 1963/2000 [1:53:53<01:58,  3.20s/it]









 98%|█████████▊| 1964/2000 [1:53:58<02:19,  3.88s/it]









 98%|█████████▊| 1965/2000 [1:54:00<01:51,  3.18s/it]



In [4]:
new_documents = json.load(open("processed_data.txt" , "r"))

### Some Stats

In [5]:
words_counter = collections.Counter([word for document,gr in new_documents for sentence in document for word in sentence.split()])

print('{} unique English words.'.format(len(words_counter)))
print('10 Most common words in the English dataset:')
print('"' + '" "'.join(list(zip(*words_counter.most_common(10)))[0]) + '"')

20025 unique English words.
10 Most common words in the English dataset:
"the" "." "to" "," "and" "of" "i" "a" "in" "that"


Tokenization and padding to make length of all sentence of equal length

In [6]:
def get_tokenizer(x):
    """
    Tokenize x
    :param x: List of sentences/strings to be tokenized
    :return: Tuple of (tokenized x data, tokenizer used to tokenize x)
    """
    # TODO: Implement
    tokenizer = Tokenizer(filters='')
    tokenizer.fit_on_texts(x)
    
    return tokenizer

def tokenize_text(tokenizer, x):
    return tokenizer.texts_to_sequences(x),

# Tokenize Example output

In [7]:
def pad(x, length=None):
    """
    Pad x
    :param x: List of sequences.
    :param length: Length to pad the sequence to.  If None, use length of longest sequence in x.
    :return: Padded numpy array of sequences
    """
    
    return pad_sequences(x, maxlen = length, padding = 'post')


# Pad Tokenized output

In [8]:
def preprocess(tokenizer, documents):
    """
    Preprocess x and y
    :param x: Feature List of sentences
    :param y: Label List of sentences
    :return: Tuple of (Preprocessed x, Preprocessed y, x tokenizer, y tokenizer)
    """
    preprocess_x = [pad(tokenizer.texts_to_sequences(doc), 41) for doc in documents] 

    # Keras's sparse_categorical_crossentropy function requires the labels to be in 3 dimension

    return preprocess_x



In [9]:
# Join all documents to create sentences
# Using those sentences create a tokenizer for both gr and words

all_sentences = [' '.join(doc)for doc, gr in new_documents]

all_gr = [' '.join([' '.join(j) for j in gr]) for doc, gr in new_documents]



In [10]:
sentence_tokenizer = get_tokenizer(all_sentences)
gr_tokenizer = get_tokenizer(all_gr)

In [11]:
documents = [doc for doc, gr in new_documents]
gr = [[' '.join(g)for g in gr] for doc, gr in new_documents ]



In [12]:
preprocess_sentence = preprocess(sentence_tokenizer, documents)
preprocess_gr = preprocess(gr_tokenizer, gr)

In [13]:
class Attention(Layer):
    def __init__(self, **kwargs):
        self.supports_masking = True
        self.trainable = True
        self.init_stdev = 0.01
        super(Attention, self).__init__(**kwargs)

    def build(self, input_shape):
        init_val_v = (randm.randn(input_shape[2]) * self.init_stdev).astype(K.floatx())
        self.att_v = K.variable(init_val_v, name='att_v')
        init_val_W = (randm.randn(input_shape[2], input_shape[2]) * self.init_stdev).astype(K.floatx())
        self.att_W = K.variable(init_val_W, name='att_W')
        self.trainable_weights = [self.att_v, self.att_W]
    
    def call(self, x, mask=None):
        y = K.dot(x, self.att_W)
        weights = K.tf.tensordot(self.att_v, K.tanh(y), axes=[[0], [2]])
        weights = K.softmax(weights)
        out = x * K.permute_dimensions(K.repeat(weights, x.shape[2]), [0, 2, 1])
        out = K.sum(out, axis=1)
        return K.cast(out, K.floatx())

    def get_output_shape_for(self, input_shape):
        return (input_shape[0], input_shape[2])
    
    def compute_mask(self, x, mask):
        return None
    
    def compute_output_shape(self, input_shape):
        return (input_shape[0], input_shape[2])

In [14]:
def read_emb(emb_path):
    embeddings = {}
    with open(emb_path, 'r') as f:
        for line in f:
            values = line.split()
            word = values[0]
            coefs = np.asarray(values[1:], dtype=K.floatx())
            embeddings[word] = coefs
    f.close()
    return embeddings

def get_emb_matrix_given_vocab(vocab, source_emb_matrix, dest_emb_matrix, emb_dim):
    counter = 0.
    for word, index in vocab.items(): #vocab.iteritems() in python2
        try:
            if index == 0:
                dest_emb_matrix[index] = np.zeros(emb_dim, dtype=K.floatx())
            else:
                dest_emb_matrix[index] = source_emb_matrix[word]
            counter += 1
        except KeyError:
            pass
    return dest_emb_matrix


In [31]:
def create_model(args, vocab, vocab_size, grs_size):
    embeddings = read_emb(args['emb_path'])
    embedding_matrix = np.random.normal(loc=0.0, scale=0.01, size=(vocab_size, args['emb_dim']))
    emb_main = Embedding(vocab_size, args['emb_dim'], mask_zero=True, weights=[get_emb_matrix_given_vocab(vocab, embeddings, embedding_matrix, args['emb_dim'])]) 

    sequence = Input(shape=(None,args['max_sentence_length'] ),
              dtype='int32', name='main_input')
    
    embedded_sent = TimeDistributed(emb_main)(sequence)
    embedded_sent = Dropout(args['dropout'])(embedded_sent)
    rnn_sent = TimeDistributed(Bidirectional(LSTM(args['rnn_dim'], return_sequences=True),merge_mode='concat'))(embedded_sent)
    #predict gr roles
    n_tags = grs_size
    grs = TimeDistributed(TimeDistributed(Dense(n_tags, activation="softmax")), name='gr_scores')(rnn_sent)
    rnn_sent = TimeDistributed(Attention())(rnn_sent)

    merged = Bidirectional(LSTM(args['rnn_dim'], return_sequences=True),merge_mode='concat')(rnn_sent)
    merged = Dropout(args['dropout'])(merged)
    mot = Attention()(merged)
    dense = Dense(3)(mot)
    score_gc = Activation('softmax', name='score')(dense)
    model = Model(input=sequence, output=[score_gc, grs])
    if args['model_path'] != "":
        model.load_weights(args['model_path'], by_name=True)
    model.summary()
    return model

args = {}
args['emb_path'] = "glove.6B.50d.txt"
args['emb_dim'] = 50
args['max_sentence_length'] = 41
args['dropout'] = 0.5
args['model_path'] = ""
args['rnn_dim'] = 2
grs_size = 39
vocab = sentence_tokenizer.word_index
vocab_size = len(sentence_tokenizer.word_index)+1
model = create_model(args,vocab ,vocab_size , grs_size)


/home/dheeraj/.local/lib/python3.5/site-packages/ipykernel_launcher.py:22: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=[<tf.Tenso..., inputs=Tensor("ma...)`


____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
main_input (InputLayer)          (None, None, 41)      0                                            
____________________________________________________________________________________________________
time_distributed_9 (TimeDistribu (None, None, 41, 50)  1000650                                      
____________________________________________________________________________________________________
dropout_5 (Dropout)              (None, None, 41, 50)  0                                            
____________________________________________________________________________________________________
time_distributed_10 (TimeDistrib (None, None, 41, 4)   848                                          
___________________________________________________________________________________________

In [32]:
# Optimizing model and defining loss function
opt = RMSprop(lr=0.001)
losses = { "score": "mean_squared_error", "gr_scores": "categorical_crossentropy"}
loss_weights =  {"score" : 1 , "gr_scores":0.1}
model.compile(optimizer=opt, loss=losses, loss_weights=loss_weights)

In [19]:
# Training sentences are in preprocess_sentence
# label of sentences in label
# Label for GR in preprocess_gr

categorical_label = np_utils.to_categorical(list(map(lambda x:x-1,label)), num_classes=3)

In [ ]:
import time
def generator_training():
    while True:
        
        for j,doc in enumerate(preprocess_sentence):
            yield (np.array([preprocess_sentence[j]]),{"score": np.array(categorical_label[j]).reshape(-1,3), "gr_scores": np.array([cat_doc[j]])})
        
itera = generator_training()
model.fit_generator(itera, epochs=25, steps_per_epoch=2000, )

Epoch 1/25
1693/2000 [========================>.....] - ETA: 16s - loss: 0.3771 - score_loss: 0.2111 - gr_scores_loss: 1.6601

In [20]:
categorical_gr = []
cat_doc = []
for doc in preprocess_gr:
    
    cat_sent = []
    for each_sent in doc:
        
        temp = []
        for index in each_sent:
            
            label = np.array([0] * 39)
            label[index - 1] = 1
            temp.append(label)
        cat_sent.append(temp)
    cat_doc.append(cat_sent)
            

In [158]:
list(generator_training(preprocess_sentence))


[(array([[[  230,    60,    23,    14,     9,     8,   110,   246,     3,
             565,  4464,     3,   465,  9447,  1561,    71,   124,    15,
           18221,     9,   462,    78,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0],
          [   30,    47,     4,     7,    28,  1026,    14,   359,    74,
               3,   261,    15,   462,  2183,     5,     7,    19,    61,
               1,  7077,   223,     3,   307,     1,  4464,     2,     0,
               0,     0,     0,     0,     0,     0,     0,     0,     0,
               0,     0,     0,     0,     0],
          [   57,    12,  2219,   170,     4,    70,    19,  3090,    74,
               3,   608,  1388,    12,  2679,     4,  4942,   929, 19375,
               4,   402,     4,     5,    18,  2219,   146,   612,    19,
            2695,    74,   144,     1,   192,     6,     1,   398,    15,
             508, 